# COVID-19 Case Growth by County
This notebook looks at COVID-19 case and fatality growth rates in the US by county. Since we are past the exponential growth phase of the pandemic this notebook simply looks at percentage growth/reduction over the past 7 days.

In [74]:
import pandas as pd
import geopandas as gpd
import numpy as np
import matplotlib as plt
import folium
from folium import Choropleth, Circle, Marker
from folium.plugins import HeatMap, MarkerCluster

In [75]:
us_center=[37, -98.5795]
# real US center is [39.8283, -98.5795] but we move the center
# a bit south to leave space for the legend

In [76]:
# function to convert a fips code to a zero-padded string
def fips2str(x):
    return str(int(x)).zfill(5) if x== x else x

In [77]:
# read directly from NYT's github repo for the freshest data
counties = pd.read_csv('https://raw.githubusercontent.com/nytimes/covid-19-data/master/us-counties.csv')

# convert fips codes to strings
counties['fips'] = counties['fips'].apply(fips2str)

counties.tail()

date      county    state   fips  cases  deaths
227684  2020-06-11  Sweetwater  Wyoming  56037     36       0
227685  2020-06-11       Teton  Wyoming  56039    102       1
227686  2020-06-11       Uinta  Wyoming  56041     53       0
227687  2020-06-11    Washakie  Wyoming  56043     38       3
227688  2020-06-11      Weston  Wyoming  56045      1       0

In [78]:
counties.loc[counties.fips=='36999']

Empty DataFrame
Columns: [date, county, state, fips, cases, deaths]
Index: []

In [79]:
# get the county geometries for mapping
counties_geometry = gpd.read_file('counties.json')
counties_geometry.head()

id          GEO_ID STATE COUNTY      NAME    LSAD  CENSUSAREA  \
0  01001  0500000US01001    01    001   Autauga  County     594.436   
1  01009  0500000US01009    01    009    Blount  County     644.776   
2  01017  0500000US01017    01    017  Chambers  County     596.531   
3  01021  0500000US01021    01    021   Chilton  County     692.854   
4  01033  0500000US01033    01    033   Colbert  County     592.619   

                                            geometry  
0  POLYGON ((-86.49677 32.34444, -86.71790 32.402...  
1  POLYGON ((-86.57780 33.76532, -86.75914 33.840...  
2  POLYGON ((-85.18413 32.87053, -85.12342 32.772...  
3  POLYGON ((-86.51734 33.02057, -86.51596 32.929...  
4  POLYGON ((-88.13999 34.58170, -88.13925 34.587...

In [80]:
# We don't need many of these columns so let's drop them
counties_geometry = counties_geometry.drop(
    columns=['GEO_ID','STATE','COUNTY','NAME','LSAD','CENSUSAREA']
)

In [81]:
populations = pd.read_csv('county_populations.csv')
populations['fips'] = populations['fips'].apply(fips2str)
populations.head()

fips State          County  Population
0  00000    US   United States   327167434
1  01000    AL         Alabama     4887871
2  01001    AL  Autauga County       55601
3  01003    AL  Baldwin County      218022
4  01005    AL  Barbour County       24881

In [82]:
# the geopandas dataframe needs to be on the left of any merge
# for the result to still be a geopandas object
counties_roc = counties_geometry.merge(populations,left_on='id',right_on='fips')

In [83]:
counties_roc.head()

id                                           geometry   fips State  \
0  01001  POLYGON ((-86.49677 32.34444, -86.71790 32.402...  01001    AL   
1  01009  POLYGON ((-86.57780 33.76532, -86.75914 33.840...  01009    AL   
2  01017  POLYGON ((-85.18413 32.87053, -85.12342 32.772...  01017    AL   
3  01021  POLYGON ((-86.51734 33.02057, -86.51596 32.929...  01021    AL   
4  01033  POLYGON ((-88.13999 34.58170, -88.13925 34.587...  01033    AL   

            County  Population  
0   Autauga County       55601  
1    Blount County       57840  
2  Chambers County       33615  
3   Chilton County       44153  
4   Colbert County       54762

In [84]:
# Make a fake FIPS for NYC. NY state FIPS are 36xxx.
# We can use 36999 but need to union the polygons for the 5 counties
# 36047, 36081, 36061, 36085, 36005
# New York county is 36061
nyc_fips = ['36047', '36081', '36061', '36085', '36005']
nyc_population = populations.loc[populations['fips'].isin(nyc_fips),'Population'].sum()

In [85]:
# get the geometries of the 5 NYC counties and merge them
# see https://deparkes.co.uk/2015/02/28/how-to-merge-polygons-in-python/
from shapely.ops import cascaded_union

nyc_geo = cascaded_union(
    counties_geometry.loc[
        counties_geometry.id.isin(nyc_fips),
        'geometry'
    ])

In [86]:
# create a synthetic county in the county geometry dataframe for NYC
counties_roc = counties_roc.append(
    [{'id': '36999', 'geometry': nyc_geo, 'fips': '36999', 'State': 'NY', 'County': 'New York City', 'Population': nyc_population}])

nyc_index = counties_roc.loc[counties_roc['fips'].isin(nyc_fips)].index
counties_roc.drop(index=nyc_index,inplace=True)
# use the fake fips code for all the NYC data
counties.loc[counties.county=='New York City','fips'] = '36999'
counties_roc.drop(index=counties_roc.loc[counties_roc['id'].isin(nyc_fips)].index,inplace=True)

In [87]:
# define a function to compute the rate of change in cases/deaths over the past 2 periods
def case_roc(code,dim='cases',period=7):
    accel = np.nan
    roc = np.nan    
    try:
        end_current_period = counties.loc[counties['fips']==code,dim][-1:].item()
        end_past_period = counties.loc[counties['fips']==code,dim][-period-1:-period].item()
        beginning_past_period = counties.loc[counties['fips']==code,dim][-2*period-1:-2*period].item()
        current_period = max(end_current_period - end_past_period,0)
        past_period = max(end_past_period - beginning_past_period,0)
        if past_period != 0:
            roc = 100*(1 - (current_period/past_period))
    except:
        pass
    return roc

In [88]:
counties_roc['ric'] = counties_roc.fips.apply(lambda x: case_roc(x,period=14))
counties_roc['ric_deaths'] = counties_roc.fips.apply(lambda x: case_roc(x,dim='deaths',period=14))
counties_roc.set_index('fips',inplace=True) # needed for folium to work
counties_roc['ric'] = counties_roc['ric'].clip(-100,100)
counties_roc['total_cases'] = counties.groupby('fips').agg({'cases': max})

In [90]:
# from suggestion at https://github.com/python-visualization/folium/issues/1202#issue-489232629
def add_title(m,title,subtitle):
    title_html = '<p align="center" style="font-size:18px; margin-bottom:0px; font-weight:bold">{}</p>'.format(title)
    if subtitle:
        title_html = title_html + '<p align="center" style="font-size:14px; font-style:italic">{}</p>'.format(subtitle)
    m.get_root().html.add_child(folium.Element(title_html))

In [91]:
m = folium.Map(tiles='cartodbpositron',location=us_center,zoom_start=4)
Choropleth(geo_data=counties_roc.__geo_interface__, 
           data=counties_roc.loc[counties_roc['total_cases']>10,'ric'], 
           key_on="feature.properties.id",
           fill_color='RdYlGn',
           nan_fill_color='#f2f2f2',
           line_weight=0.5,
           line_opacity=0.5,
           smooth_factor=0.1
          ).add_to(m)
add_title(m,
          '% Reduction in new cases, last 2 weeks compared to previous 2 weeks',
          'Counties with >10 cases. Green is better, red is worse (more cases)'
)
m

In [93]:
def map_state(state):
    tmp = counties_roc.loc[counties_roc.State == state]
    centroid = cascaded_union(tmp.geometry).centroid.coords[0][::-1]
    m = folium.Map(tiles='cartodbpositron',location=centroid,zoom_start=6)
    Choropleth(geo_data=tmp.__geo_interface__, 
               data=tmp.ric, 
               key_on="feature.properties.id",
               fill_color='RdYlGn',
               nan_fill_color='#f2f2f2',
               line_weight=0.5,
               line_opacity=0.5,
               smooth_factor=0.1
              ).add_to(m)
    add_title(m,
              '% Reduction in new cases for {}, last 2 weeks vs. previous 2 weeks'.format(state),
              'Green is better, red is worse (more cases)')
    display(m)

In [94]:
map_state('MN')

In [95]:
map_state('AL')

In [96]:
map_state('GA')

In [97]:
map_state('NY')

In [98]:
map_state('CA')

In [99]:
map_state('UT')

In [100]:
map_state('MO')

In [103]:
map_state('FL')